# FinBert

FinBert is a sentiment Analysis AI for Financial text.
Since we want to evaluate news article this is a necessary feature to analyse those texts.
In this document a first use of this tool will be shown.
Some texts will be analysed. Especially the analysis of german texts will be tried.

## Sources

[HugginFace](https://huggingface.co/ProsusAI/finbert)
[Tutorial](https://medium.com/codex/stocks-news-sentiment-analysis-with-deep-learning-transformers-and-machine-learning-cdcdb827fc06)

## Libraries

* transformers
* tqdm
* pandas
* numpy
* torch
* torchvision
* torchaudio

In [1]:
!pip install transformers tqdm pandas numpy torch torchvision torchaudio -U


[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


### Importing and creation of models and tokenizer

In [2]:
import pandas as pd
import torch

from transformers import AutoTokenizer, AutoModelForSequenceClassification

# create a tokenizer object
tokenizer = AutoTokenizer.from_pretrained("ProsusAI/finbert")

# fetch the pretrained model
model = AutoModelForSequenceClassification.from_pretrained("ProsusAI/finbert")

C:\Users\phhor\PycharmProjects\aki_prj23_transparenzregister\venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Analyze a single sentiment

In [3]:
def analyze_sentiment(text: str) -> pd.Series:
    print(text)
    input_tokens = tokenizer(text, padding=True, truncation=True, return_tensors="pt")
    output = model(**input_tokens)
    return pd.Series(
        torch.nn.functional.softmax(output.logits, dim=-1)[0].data,
        index=["+", "0", "-"],
    )


headline = "Microsoft fails to hit profit expectations"
tf = analyze_sentiment(headline)
tf

Microsoft fails to hit profit expectations


+    0.034084
0    0.932933
-    0.032982
dtype: float32

### Creating test data

In [4]:
text_df = pd.DataFrame(
    [
        {"text": "Microsoft fails to hit profit expectations", "lan": "en"},
        {
            "text": "Am Aktienmarkt überwieg weiter die Zuversicht, wie der Kursverlauf des DAX zeigt.",
            "lan": "de",
        },
        {"text": "Stocks rallied and the British pound gained.", "lan": "en"},
        {
            "text": "Meyer Burger bedient ab sofort australischen Markt und präsentiert sich auf Smart Energy Expo in Sydney.",
            "lan": "de",
        },
        {
            "text": "Meyer Burger enters Australian market and exhibits at Smart Energy Expo in Sydney.",
            "lan": "en",
        },
        {
            "text": "J&T Express Vietnam hilft lokalen Handwerksdörfern, ihre Reichweite zu vergrößern.",
            "lan": "en",
        },
        {
            "text": "7 Experten empfehlen die Aktie zum Kauf, 1 Experte empfiehlt, die Aktie zu halten.",
            "lan": "de",
        },
        {"text": "Microsoft aktie fällt.", "lan": "de"},
        {"text": "Microsoft aktie steigt.", "lan": "de"},
    ]
)
text_df

text lan
0         Microsoft fails to hit profit expectations  en
1  Am Aktienmarkt überwieg weiter die Zuversicht,...  de
2       Stocks rallied and the British pound gained.  en
3  Meyer Burger bedient ab sofort australischen M...  de
4  Meyer Burger enters Australian market and exhi...  en
5  J&T Express Vietnam hilft lokalen Handwerksdör...  en
6  7 Experten empfehlen die Aktie zum Kauf, 1 Exp...  de
7                             Microsoft aktie fällt.  de
8                            Microsoft aktie steigt.  de

In [6]:
### Analyze multiple Sentiments

In [5]:
def analyse_sentiments(texts: pd.DataFrame) -> pd.DataFrame:
    values = texts["text"].apply(analyze_sentiment)
    texts[["+", "0", "-"]] = values
    return texts


analyse_sentiments(text_df)

Microsoft fails to hit profit expectations
Am Aktienmarkt überwieg weiter die Zuversicht, wie der Kursverlauf des DAX zeigt.
Stocks rallied and the British pound gained.
Meyer Burger bedient ab sofort australischen Markt und präsentiert sich auf Smart Energy Expo in Sydney.
Meyer Burger enters Australian market and exhibits at Smart Energy Expo in Sydney.
J&T Express Vietnam hilft lokalen Handwerksdörfern, ihre Reichweite zu vergrößern.
7 Experten empfehlen die Aktie zum Kauf, 1 Experte empfiehlt, die Aktie zu halten.
Microsoft aktie fällt.
Microsoft aktie steigt.


text lan         +         0   
0         Microsoft fails to hit profit expectations  en  0.034084  0.932933  \
1  Am Aktienmarkt überwieg weiter die Zuversicht,...  de  0.053528  0.027950   
2       Stocks rallied and the British pound gained.  en  0.898361  0.034474   
3  Meyer Burger bedient ab sofort australischen M...  de  0.116597  0.012790   
4  Meyer Burger enters Australian market and exhi...  en  0.187527  0.008846   
5  J&T Express Vietnam hilft lokalen Handwerksdör...  en  0.066277  0.020608   
6  7 Experten empfehlen die Aktie zum Kauf, 1 Exp...  de  0.050346  0.022004   
7                             Microsoft aktie fällt.  de  0.066061  0.016440   
8                            Microsoft aktie steigt.  de  0.041449  0.018471   

          -  
0  0.032982  
1  0.918522  
2  0.067165  
3  0.870613  
4  0.803627  
5  0.913115  
6  0.927650  
7  0.917498  
8  0.940080

## Conclusion

The current form of this model can't be used for the german language.
It could be used if the text is translated beforehand. But it is questionable if that will work well.
Another way would be to retrain the same model with translated text from this models' data. But I do not believe this to be feasible.